# Binary classification with the crabs data

In this example we show how the GP Monte Carlo function can be used for supervised learning classification. We use the Crab dataset from the R package MASS. In this dataset we are interested in predicting whether a crab is of colour form blue or orange.

In [1]:
using GaussianProcesses

train=readdlm("data/crabs_train.txt",',');

train[train[:,1].==-1.0,1]=0.0;
y = convert(Vector{Bool},train[:,1]);       # response
X = train[:,2:end];                         # predictors

We assume a zero mean GP with a Matern 3/2 kernel. We use the automatic relevance determination (ARD) kernel to allow each dimension of the predictor variables to have a different length scale. As this is binary classifcation, we use the Bernoulli likelihood.

In [2]:
#Select mean, kernel and likelihood function
mZero = MeanZero()   #Zero mean function
kern = Matern(3/2,zeros(5),0.0)   #Matern 3/2 ARD kernel (note that hyperparameters are on the log scale)
lik = BernLik()

Type: GaussianProcesses.BernLik, Params: Any[]


We fit the GP using the general `GP` function. This function is a shorthand for the `GPMC` function which is used to generate Monte Carlo approximations of the latent function when the likelihood is non-Gaussian. 

In [3]:
gp = GP(X',vec(y),mZero,kern,lik)

GP Monte Carlo object:
  Dim = 5
  Number of observations = 100
  Mean function:
    Type: GaussianProcesses.MeanZero, Params: Float64[]
  Kernel:
    Type: GaussianProcesses.Mat32Ard, Params: [-0.0,-0.0,-0.0,-0.0,-0.0,0.0]
  Likelihood:
    Type: GaussianProcesses.BernLik, Params: Any[]
  Input observations = 
[8.1 8.8 … 17.5 19.2; 6.7 7.7 … 16.7 16.5; … ; 19.0 20.8 … 44.5 47.9; 7.0 7.4 … 17.0 18.1]
  Output observations = Bool[false,false,false,false,false,false,false,false,false,false  …  true,true,true,true,true,true,true,true,true,true]
  Log-posterior = -161.209

In [ ]:
We assign Normal priors to each of the Matern 3/2 kernel parameters.

In [4]:
GaussianProcesses.set_priors!(gp.k,[Distributions.Normal(0.0,2.0) for i in 1:6])

6-element Array{Distributions.Normal{Float64},1}:
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)

Samples of the latent function $f|X,y,\theta$ are drawn using MCMC sampling. The MCMC routine uses the `Klara` package. By default, the `mcmc` function uses the MALA algorithm, where the stepsize is automatically tuned to a desired acceptance rate. Alternative samplers, such as HMC and NUTS, can also be used. 

In [5]:
samples = mcmc(gp)

BasicMCJob:
  Variable [1]: p (Klara.BasicContMuvParameter)
  GenericModel: 1 variables, 0 dependencies (directed graph)
  MALA sampler: drift step = 0.1
  VanillaMCTuner: period = 100, verbose = false
  BasicMCRange: number of steps = 5000, burnin = 1000, thinning = 1
  plain = true (job flow not controlled by tasks)

106×4000 Array{Float64,2}:
 -1.24239     -1.24239     -1.24239     …  -0.442346   -0.442346   -0.442346 
 -0.441167    -0.441167    -0.441167       -0.411605   -0.411605   -0.411605 
 -0.589553    -0.589553    -0.589553        0.904812    0.904812    0.904812 
  1.36738      1.36738      1.36738        -0.770789   -0.770789   -0.770789 
  1.72254      1.72254      1.72254         1.87082     1.87082     1.87082  
 -0.720687    -0.720687    -0.720687    …  -0.987837   -0.987837   -0.987837 
  0.0451916    0.0451916    0.0451916       0.824584    0.824584    0.824584 
 -1.62355     -1.62355     -1.62355        -1.89175    -1.89175    -1.89175  
  0.584583     0.584583     0.584583       -0.0633453  -0.0633453  -0.0633453
  0.00396535   0.00396535   0.00396535     -0.094304   -0.094304   -0.094304 
 -1.4073      -1.4073      -1.4073      …  -0.442891   -0.442891   -0.442891 
  2.12682      2.12682      2.12682         0.509948    0.509948    0.509948 
 -0.203422    -0.203422    -0.203422 

We test the predictive accuracy of the fitted model against a hold-out dataset

In [6]:
test = readdlm("data/crabs_test.txt",',');
test[test[:,1].==-1.0,1]=0.0;

xTest = test[:,2:end];
yTest = test[:,1];

100-element Array{Float64,1}:
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 ⋮  
 1.0
 1.0
 1.0
 1.0
 1.0
 1.0
 1.0
 1.0
 1.0
 1.0
 1.0
 1.0

In [7]:
ymean = Array(Float64,size(samples,2),size(xTest,1));

for i in 1:size(samples,2)
    GaussianProcesses.set_params!(gp,samples[:,i])
    GaussianProcesses.update_target!(gp)
    ymean[i,:] = predict_y(gp,xTest')[1]
end

In [8]:
using Plots
gr()

plot(ymean',leg=false)
scatter!(yTest)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0 
 
 
 50 
 
 
 100 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
<polyline clip-path="url(#clip02)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,358.046 60.2815,76.9178 65.5488,20.2417 70.8162,21.7133 76.0835,69.6667 81.3509,316.604 86.6182,275.753 91.8856,346.659 97.1529,355.544 102.42,342.692 
 107.688,36.8091 112.955,358.21 118.222,358.227 123.49,357.862 128.757,358.244 134.024,357.761 139.292,119.739 144.559,172.362 149.826,256.921 155.094,114.433 
 160.361,100.276 165.629,278.539 170.896,19.2844 176.163,161.948 181.431,100.693 186.698,288.221 191.965,302.407 197.233,303.017 202.5,232.42 207.767,313.553 
 213.035,356.81 218.302,332.482 223.569,352.095 228.837,352.658 234.104,346.198 239.371,193.87 244.639,307.058 249.906,357.689 255.173,348.796 260.441,357.937 
 265.708,358.296 270.976,357.815 276.243,356.095 281.51,339.523 286.778,342.789 292.045,354.412 297.312,323.893 302.58,323.32 307.847,233.515 313.114,326.543 
 318.382,18.0817 323.649,18.0811 328.916,250.492 334.184,18.0967 339.451,18.1323 344.718,19.0598 349.986,29.3542 355.253,18.1017 360.521,32.9585 365.788,20.476 
 371.055,18.8766 376.323,26.1608 381.59,25.9659 386.857,55.3942 392.125,31.2197 397.392,18.5256 402.659,18.26 407.927,20.8217 413.194,18.6134 418.461,20.6619 
 423.729,18.176 428.996,19.0759 434.263,27.6501 439.531,18.6247 444.798,27.1897 450.066,85.5975 455.333,60.1347 460.6,51.9779 465.868,75.6837 471.135,127.767 
 476.402,22.83 481.67,49.2107 486.937,89.6323 492.204,108.934 497.472,99.6599 502.739,91.1534 508.006,98.7122 513.274,121.976 518.541,94.7964 523.808,82.4267 
 529.076,190.743 534.343,103.86 539.61,110.637 544.878,134.038 550.145,159.881 555.413,133.372 560.68,115.392 565.947,123.236 571.215,147.804 576.482,186.229 
 
 "/>
<polyline clip-path="url(#clip02)" style="stroke:#e26f46; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,358.046 60.2815,76.9178 65.5488,20.2417 70.8162,21.7133 76.0835,69.6667 81.3509,316.604 86.6182,275.753 91.8856,346.659 97.1529,355.544 102.42,342.692 
 107.688,36.8091 112.955,358.21 118.222,358.227 123.49,357.862 128.757,358.244 134.024,357.761 139.292,119.739 144.559,172.362 149.826,256.921 155.094,114.433 
 160.361,100.276 165.629,278.539 170.896,19.2844 176.163,161.948 181.431,100.693 186.698,288.221 191.965,302.407 197.233,303.017 202.5,232.42 207.767,313.553 
 213.035,356.81 218.302,332.482 223.569,352.095 228.837,352.658 234.104,346.198 239.371,193.87 244.639,307.058 249.906,357.689 255.173,348.796 260.441,357.937 
 265.708,358.296 270.976,357.815 276.243,356.095 281.51,339.523 286.778,342.789 292.045,354.412 297.312,323.893 302.58,323.32 307.847,233.515 313.114,326.543 
 318.382,18.0817 323.649,18.0811 328.916,250.492 334.184,18.0967 339.451,18.1323 344.718,19.0598 349.986,29.3542 355.253,18.1017 360.521,32.9585 365.788,20.476 
 371.055,18.8766 376.323,26.1608 381.59,25.9659 386.857,55.3942 392.125,31.2197 397.392,18.5256 402.659,18.26 407.927,20.8217 413.194,18.6134 418.461,20.6619 
 423.729,18.176 428.996,19.0759 434.263,27.6501 439.531,18.6247 444.798,27.1897 450.066,85.5975 455.333,60.1347 460.6,51.9779 465.868,75.6837 471.135,127.767 
 476.402,22.83 481.67,49.2107 486.937,89.6323 492.204,108.934 497.472,99.6599 502.739,91.1534 508.006,98.7122 513.274,121.976 518.541,94.7964 523.808,82.4267 
 529.076,190.743 534.343,103.86 539.61,110.637 544.878,134.038 550.145,159.881 555.413,133.372 560.68,115.392 565.947,123.236 571.215,147.804 576.482,186.229 
 
 "/>
<polyline clip-path="url(#clip02)" style="stroke:#3da44d; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,358.046 60.2815,76.9178 65.5488,20.2417 70.8162,21.7133 76.0835,69.6667 81.3509,316.604 86.6182,275.753 91.8856,346.659 97.1529,355.544 102.42,342.692 
 107.688,36.8091 112.955,358.21 118.222,358.227 123.49,357.862 128.757,358.244 134.024,357.761 139.292,119.739 144.559,172.362 149.826,25